In [1]:
from preprocessing.settings import *
from keras.models import Sequential
from keras.layers import LSTM, Dense, Activation, Embedding
from keras.optimizers import RMSprop, Adam
# from keras.utils import to_categorical
from keras.utils import np_utils
from keras.layers.wrappers import Bidirectional
from random import shuffle
import progressbar
import matplotlib
matplotlib.use('Agg')
import matplotlib.pyplot as plt
import os
import numpy as np
import _pickle as pickle
from keras import backend as K
from preprocessing import data_class
# import chord_model

import keras
import tensorflow as tf
from keras.backend.tensorflow_backend import set_session

Using TensorFlow backend.


In [2]:
def get_chord_dict():
    chord_to_index = pickle.load(open(dict_path + chord_dict_name, 'rb'))
    index_to_chord = pickle.load(open(dict_path + index_dict_name, 'rb'))
    return chord_to_index, index_to_chord

In [3]:
# chord_model file class
class Embed_Chord_Model:
    
    def __init__(self, model_path):
        
        print('loading chord model ...')
        
        model = keras.models.load_model(model_path)
        model.reset_states()
        self.embed_layer_output = K.function([model.layers[0].input], [model.layers[0].output])
        self.chord_to_index, self.index_to_chords = get_chord_dict()        
        
    
    
    def embed_chord(self, chord):
        print(self.embed_layer_output(chord)[0])
        return self.embed_layer_output(chord)[0]
    
    
    def embed_chords_song(self, chords):
        
        embeded_chords = []
        
        for chord in chords:
            embeded_chords.append(self.embed_chord(chord))
            
        return embeded_chords

In [4]:
# Path to the fully trained chord model for the chord embeddings:
chord_model_path = 'models/chords/model_Epoch50_4.pickle'
# Path where the polyphonic models are saved:
model_path = 'models/chords_mldy/'
model_filetype = '.pickle'


In [5]:
epochs = 100
train_set_size = 4
test_set_size = 1
test_step = 360          # Calculate error for test set every this many songs

verbose = False
show_plot = False
save_plot = True
lstm_size = 512
batch_size = 1
learning_rate = 1e-06
step_size = 1
save_step = 1
shuffle_train_set = True
bidirectional = False
embedding = False
optimizer = 'Adam'

In [6]:
fd = {'shifted': shifted, 'next_chord_feature': next_chord_feature, 'chord_embed_method': chord_embed_method, 'counter': counter_feature, 'highcrop': high_crop, 'lowcrop':low_crop, 'lr': learning_rate, 'opt': optimizer,
'bi': bidirectional, 'lstms': lstm_size, 'trainsize': train_set_size, 'testsize': test_set_size}
model_name = "polyphonic_lstm_training"

In [7]:
print('loading data...')
# Get Train and test sets
train_set, test_set, chord_train_set, chord_test_set = data_class.get_ind_train_and_test_set(train_set_size, test_set_size)

if chord_embed_method == 'embed':
    chord_dim = chord_embedding_dim
elif chord_embed_method == 'onehot':
    chord_dim = num_chords
elif chord_embed_method == 'int':
    chord_dim = 1

if next_chord_feature:
    chord_dim = chord_dim*2

loading data...


In [8]:
train_set, test_set, chord_train_set, chord_test_set

([[(),
   (),
   (),
   (),
   (),
   (),
   (),
   (),
   (55, 60),
   (55, 60),
   (55, 60),
   (55, 59),
   (55, 59),
   (55, 59),
   (55, 59),
   (55, 59),
   (55, 60),
   (55, 60),
   (55, 60),
   (55, 59),
   (55, 59),
   (55, 59),
   (55, 59),
   (55, 59),
   (55, 60),
   (55, 60),
   (55, 60),
   (55, 59),
   (55, 59),
   (55, 59),
   (55, 59),
   (55, 59),
   (55, 60),
   (55, 60),
   (55, 60),
   (55, 59),
   (55, 59),
   (55, 59),
   (55, 59),
   (55, 59),
   (48, 55, 60, 64, 67),
   (48, 55, 60, 64, 67),
   (48, 55, 60, 64, 67),
   (47, 55, 59, 62, 67),
   (47, 55, 59, 62, 67),
   (47, 55, 59, 62, 64, 67),
   (47, 55, 59, 64, 67),
   (45, 52, 57, 60, 64),
   (45, 52, 57, 60, 64),
   (45, 52, 57, 60, 64),
   (45, 52, 57, 60, 64),
   (43, 50, 55, 59, 62, 67),
   (43, 50, 55, 59, 62, 67),
   (43, 50, 55, 59, 62, 67),
   (43, 50, 55, 59, 60, 62, 67),
   (41, 48, 53, 57, 60, 65),
   (41, 48, 53, 57, 60, 65),
   (41, 48, 53, 57, 60, 65),
   (41, 48, 53, 57, 60, 65),
   (41, 48, 5

In [9]:
# Load model for chord embeddings
chord_embed_model = Embed_Chord_Model(chord_model_path)

loading chord model ...


C:\Users\Dax\AppData\Local\Continuum\anaconda3\lib\site-packages\tensorflow_core\python\framework\indexed_slices.py:424: UserWarning: Converting sparse IndexedSlices to a dense Tensor of unknown shape. This may consume a large amount of memory.
  "Converting sparse IndexedSlices to a dense Tensor of unknown shape. "


In [10]:
# Build Melody Model
print('creating model...')
model = Sequential()
# model.add(LSTM(lstm_size, batch_size=batch_size, input_shape=(step_size, new_num_notes+chord_dim+counter_size), stateful=True))
model.add(LSTM(lstm_size,  batch_input_shape=(batch_size,step_size, new_num_notes+chord_dim+counter_size), stateful=True))

model.add(Dense(new_num_notes))
model.add(Activation('sigmoid'))
if optimizer == 'RMS': optimizer = RMSprop(lr=learning_rate)
if optimizer == 'Adam': optimizer = Adam(lr=learning_rate)
loss = 'categorical_crossentropy'
model.compile(optimizer, loss)

creating model...


In [11]:
model.summary()

Model: "sequential_1"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
lstm_1 (LSTM)                (1, 512)                  1220608   
_________________________________________________________________
dense_1 (Dense)              (1, 60)                   30780     
_________________________________________________________________
activation_1 (Activation)    (1, 60)                   0         
Total params: 1,251,388
Trainable params: 1,251,388
Non-trainable params: 0
_________________________________________________________________


In [12]:
# initialize loss arrays
total_test_loss_array = [] 
total_train_loss_array = []
total_test_loss = 0
total_train_loss = 0

In [13]:
# Test function
def test():
    print('/nTesting:')
    total_test_loss = 0

    bar = progressbar.ProgressBar(maxval=test_set_size, redirect_stdout=False)
    for i, test_song in enumerate(test_set):
        X_test, Y_test = make_feature_vector(test_song, chord_test_set[i], chord_embed_method)

        loss = model.evaluate(X_test, Y_test, batch_size=batch_size, verbose=verbose)
        model.reset_states()
        total_test_loss += loss
        bar.update(i)
    total_test_loss_array.append(total_test_loss/test_set_size)
    print('/nTotal test loss: ', total_test_loss/test_set_size)
    print('-'*50)
    plt.plot(total_test_loss_array, 'b-')
    plt.plot(total_train_loss_array, 'r-')
#    plt.axis([0, epochs, 0, 5])
    if show_plot: plt.show()
    if save_plot: plt.savefig(model_path+'plot.png')
    pickle.dump(total_test_loss_array,open(model_path+'total_test_loss_array.pickle', 'wb'))
    pickle.dump(total_train_loss_array,open(model_path+'total_train_loss_array.pickle', 'wb'))

In [14]:
# Make feature vectors with the notes and the chord information

def make_feature_vector(song, chords, chord_embed_method):
    
    if  next_chord_feature:
        X = np.array(data_class.make_one_hot_note_vector(song[:(((len(chords)-1)*fs*2)-1)], num_notes))
    else:
        X = np.array(data_class.make_one_hot_note_vector(song[:((len(chords)*fs*2)-1)], num_notes))
#    print(X.shape)
    X = X[:,low_crop:high_crop]
#    print(X.shape)
    if chord_embed_method == 'embed':
        X_chords = list(chord_embed_model.embed_chords_song(chords))
    elif chord_embed_method == 'onehot':
        X_chords = data_class.make_one_hot_vector(chords, num_chords)
    elif chord_embed_method == 'int':
        X_chords = [[x] for x in chords]
    X_chords_new = []
    Y = X[1:]
    
    for j, _ in enumerate(X):
        ind = int(((j+1)/(fs*2)))
        
        if next_chord_feature:
            ind2 = int(((j+1)/(fs*2)))+1
#            print(j)
#            print(ind, ' ', ind2)
#            print(X_chords[ind].shape)
            X_chords_new.append(list(X_chords[ind])+list(X_chords[ind2]))
        else:
            X_chords_new.append(X_chords[ind])
            
    X_chords_new = np.array(X_chords_new)    
    X = np.append(X, X_chords_new, axis=1)
    
        
    
    if counter_feature:
        counter = [[0,0,0],[0,0,1],[0,1,0],[0,1,1],[1,0,0],[1,0,1],[1,1,0],[1,1,1]]
        if next_chord_feature:
            counter = np.array(counter*(len(X_chords)-1))[:-1]
        else:
            counter = np.array(counter*len(X_chords))[:-1]
        X = np.append(X, counter, axis=1)
    X = X[:-1]
    X = np.reshape(X, (X.shape[0], 1, X.shape[1]))
    
    return X, Y

In [15]:
# Save Parameters to text file
if not os.path.exists(model_path):
    os.makedirs(model_path)
with open(model_path + 'params.txt', "w") as text_file:
    text_file.write("Chord Model: %s" % chord_model_path + '/n')
    text_file.write("epochs: %s" % epochs + '/n')
    text_file.write("train_set_size: %s" % train_set_size + '/n')
    text_file.write("test_set_size: %s" % test_set_size + '/n')
    text_file.write("lstm_size: %s" % lstm_size + '/n')
    text_file.write("learning_rate: %s" % learning_rate + '/n')
    text_file.write("save_step: %s" % save_step + '/n')
    text_file.write("shuffle_train_set: %s" % shuffle_train_set + '/n')
    text_file.write("test_step: %s" % test_step + '/n')
    text_file.write("bidirectional: %s" % bidirectional + '/n')
    text_file.write("num_chords: %s" % num_chords + '/n')
    text_file.write("chord_n: %s" % chord_n + '/n')

In [16]:
# Train model

# train_set, test_set, chord_train_set, chord_test_set

print('training model...')
for e in range(1, epochs+1):
    
    print('Epoch ', e, 'of ', epochs, 'Epochs/nTraining:')
    
    # Shuffle training set order
    if shuffle_train_set:
        # Zip lists together an shuffle and unzip again
        ziperoni = list(zip(train_set, chord_train_set))
        shuffle(ziperoni)
        train_set, chord_train_set = zip(*ziperoni)

    bar = progressbar.ProgressBar(maxval=train_set_size)
    
    # Train model with each song seperatly
    for i, song in enumerate(train_set):
        X, Y = make_feature_vector(song, chord_train_set[i], chord_embed_method)
        for _ in range(3):
            hist = model.fit(X, Y, batch_size=batch_size, shuffle=False, verbose=verbose)
            model.reset_states()
        bar.update(i)
        total_train_loss += hist.history['loss'][0]
        if (i+1)%test_step is 0:
            total_train_loss = total_train_loss/test_step
            total_train_loss_array.append(total_train_loss)
            test()
            total_train_loss = 0

    if e%save_step is 0:
        print('saving model')
        model_save_path = model_path + 'model' + 'Epoch' + str(e) + model_filetype
        model.save(model_save_path)

training model...
Epoch  1 of  100 Epochs/nTraining:
[ 0.00122391  0.03517917 -0.04435894  0.03181332  0.05914142  0.02256753
  0.03849414 -0.00564279  0.02595195 -0.01031597]
[ 0.00178628 -0.01084906 -0.04775648 -0.00217386 -0.02934383 -0.0518349
 -0.00741101 -0.03656878  0.02368052  0.06603011]
[ 0.00178628 -0.01084906 -0.04775648 -0.00217386 -0.02934383 -0.0518349
 -0.00741101 -0.03656878  0.02368052  0.06603011]
[ 0.00178628 -0.01084906 -0.04775648 -0.00217386 -0.02934383 -0.0518349
 -0.00741101 -0.03656878  0.02368052  0.06603011]
[ 0.00178628 -0.01084906 -0.04775648 -0.00217386 -0.02934383 -0.0518349
 -0.00741101 -0.03656878  0.02368052  0.06603011]
[-0.06967775 -0.00270945  0.01831572  0.04434987  0.04575088  0.01141004
  0.03268839 -0.03287683  0.04127883 -0.05245904]
[-0.01018014 -0.05838075 -0.06145072  0.03377121  0.04533691  0.00847345
  0.03061293 -0.00731127  0.06918333 -0.06603172]
[ 0.07810515  0.05476998 -0.05403508  0.04329763 -0.05300081 -0.08941561
 -0.05243821 -0.0

Instructions for updating:
Use tf.where in 2.0, which has the same broadcast rule as np.where


N/A% (0 of 4) |                          | Elapsed Time: 0:00:00 ETA:  --:--:--

[ 0.02036239  0.05865614 -0.04360285  0.06251325 -0.05817811 -0.03039568
  0.05591736 -0.05729053 -0.00418029  0.06489214]
[ 0.02036239  0.05865614 -0.04360285  0.06251325 -0.05817811 -0.03039568
  0.05591736 -0.05729053 -0.00418029  0.06489214]
[ 0.02036239  0.05865614 -0.04360285  0.06251325 -0.05817811 -0.03039568
  0.05591736 -0.05729053 -0.00418029  0.06489214]
[ 0.03545002  0.03421258  0.00472936  0.04220152  0.08208841 -0.06742965
  0.01124754 -0.05481449  0.0594994  -0.00534894]
[ 0.03545002  0.03421258  0.00472936  0.04220152  0.08208841 -0.06742965
  0.01124754 -0.05481449  0.0594994  -0.00534894]
[ 0.04358718  0.03850792 -0.02898142 -0.01690875  0.02182377  0.03203363
  0.04335562  0.02271957 -0.05613495 -0.00483985]
[ 0.02036239  0.05865614 -0.04360285  0.06251325 -0.05817811 -0.03039568
  0.05591736 -0.05729053 -0.00418029  0.06489214]
[ 0.02036239  0.05865614 -0.04360285  0.06251325 -0.05817811 -0.03039568
  0.05591736 -0.05729053 -0.00418029  0.06489214]
[ 0.02036239  0.

 25% (1 of 4) |######                    | Elapsed Time: 0:00:27 ETA:   0:01:21

...

[ 0.00178628 -0.01084906 -0.04775648 -0.00217386 -0.02934383 -0.0518349
 -0.00741101 -0.03656878  0.02368052  0.06603011]
[ 0.07810515  0.05476998 -0.05403508  0.04329763 -0.05300081 -0.08941561
 -0.05243821 -0.0804512  -0.02320803  0.04282943]
[ 0.02036239  0.05865614 -0.04360285  0.06251325 -0.05817811 -0.03039568
  0.05591736 -0.05729053 -0.00418029  0.06489214]
[-0.06967775 -0.00270945  0.01831572  0.04434987  0.04575088  0.01141004
  0.03268839 -0.03287683  0.04127883 -0.05245904]
[ 0.00644792 -0.08144353 -0.00933185 -0.06383959  0.02514543  0.0043131
  0.06214883  0.06193028  0.02692047  0.01732401]
[ 0.07810515  0.05476998 -0.05403508  0.04329763 -0.05300081 -0.08941561
 -0.05243821 -0.0804512  -0.02320803  0.04282943]
[ 0.02036239  0.05865614 -0.04360285  0.06251325 -0.05817811 -0.03039568
  0.05591736 -0.05729053 -0.00418029  0.06489214]
[-0.06967775 -0.00270945  0.01831572  0.04434987  0.04575088  0.01141004
  0.03268839 -0.03287683  0.04127883 -0.05245904]
[ 0.07810515  0.05

 50% (2 of 4) |#############             | Elapsed Time: 0:00:45 ETA:   0:00:38

[ 0.00122391  0.03517917 -0.04435894  0.03181332  0.05914142  0.02256753
  0.03849414 -0.00564279  0.02595195 -0.01031597]
[ 0.00178628 -0.01084906 -0.04775648 -0.00217386 -0.02934383 -0.0518349
 -0.00741101 -0.03656878  0.02368052  0.06603011]
[ 0.00178628 -0.01084906 -0.04775648 -0.00217386 -0.02934383 -0.0518349
 -0.00741101 -0.03656878  0.02368052  0.06603011]
[ 0.00178628 -0.01084906 -0.04775648 -0.00217386 -0.02934383 -0.0518349
 -0.00741101 -0.03656878  0.02368052  0.06603011]
[ 0.00178628 -0.01084906 -0.04775648 -0.00217386 -0.02934383 -0.0518349
 -0.00741101 -0.03656878  0.02368052  0.06603011]
[-0.06967775 -0.00270945  0.01831572  0.04434987  0.04575088  0.01141004
  0.03268839 -0.03287683  0.04127883 -0.05245904]
[-0.01018014 -0.05838075 -0.06145072  0.03377121  0.04533691  0.00847345
  0.03061293 -0.00731127  0.06918333 -0.06603172]
[ 0.07810515  0.05476998 -0.05403508  0.04329763 -0.05300081 -0.08941561
 -0.05243821 -0.0804512  -0.02320803  0.04282943]
[ 0.03545002  0.0342

 75% (3 of 4) |###################       | Elapsed Time: 0:01:03 ETA:   0:00:18

saving model
